這是資料蒐集第二步，開始合併

In [2]:
import pandas as pd
import os
from time import sleep
from tqdm import tqdm, trange

# 合併api1中106與其他年份資料

到 https://amis.afa.gov.tw/veg/VegProdDayTransInfo.aspx 手動下載api1的106年資料，存在data_hand_106資料夾中

In [134]:
df = pd.DataFrame(columns=['CropCode','CropName','MarketName','TransDate','MarketCode','Upper_Price','Middle_Price','Lower_Price','Avg_Price','Trans_Quantity'])
df

Empty DataFrame
Columns: [CropCode, CropName, MarketName, TransDate, MarketCode, Upper_Price, Middle_Price, Lower_Price, Avg_Price, Trans_Quantity]
Index: []

In [135]:
# 106各類先合併成一份
for filename in os.listdir("data_new_hand_106"):
    print(filename)
    data = pd.read_excel("data_new_hand_106/"+filename,header=4,usecols=range(10))
    data.drop(data.tail(1).index,inplace=True)
    data['MarketCode'], data['MarketName'] = data['市　　場'].str.split(' ', 1).str
    data.drop('市　　場',inplace=True,axis=1)
    data['CropCode'], data['CropName'] = data['產　　品'].str.split(' ', 1).str
    data.drop('產　　品',inplace=True,axis=1)
    data['TransDate'] = data['日　　期'].str.replace('/','.')
    data.drop('日　　期',inplace=True,axis=1)
    data.drop('增減%',inplace=True,axis=1)
    data.drop('增減%.1',inplace=True,axis=1)
    data = data.rename(columns={'上價':'Upper_Price','中價':'Middle_Price','下價':'Lower_Price','平均價(元/公斤)':'Avg_Price','交易量(公斤)':'Trans_Quantity'})
    df = df.append(data)

根莖與其他.xls


/home/emma/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:6: FutureWarning: Columnar iteration over characters will be deprecated in future releases.
  
/home/emma/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:8: FutureWarning: Columnar iteration over characters will be deprecated in future releases.
  


F類_細項.xls
F類.xls
葉菜類.xls


api1的106沒有休市資料，api2有休市資料（但api2缺值較多）

In [136]:
df

CropCode   CropName MarketName  TransDate MarketCode  Upper_Price  \
0          SA0     蘿蔔 其他         台中市  106.01.01        400          3.0   
1          SA3     蘿蔔 矸仔         台中市  106.01.01        400         11.7   
2          SA6   蘿蔔 白玉蘿蔔         台中市  106.01.01        400         22.0   
3          SB1    胡蘿蔔 未洗         台中市  106.01.01        400         26.2   
4          SB2    胡蘿蔔 清洗         台中市  106.01.01        400         36.7   
...        ...        ...        ...        ...        ...          ...   
17757      LJ5  芥菜 翡翠娃娃菜         高雄市  106.12.31        800        103.0   
17758      LL0     茼蒿 其他         高雄市  106.12.31        800         18.8   
17759      LL1       茼蒿          高雄市  106.12.31        800         34.4   
17760      LN1       油菜          高雄市  106.12.31        800         30.0   
17761      LO1      甘薯葉          高雄市  106.12.31        800         47.0   

       Middle_Price  Lower_Price  Avg_Price Trans_Quantity  
0               3.0          3.0        3.0             30  
1               7.8          3.1        6.6           6886  
2              14.4         11.5       14.2           1113  
3              17.5          7.0       15.9            596  
4              25.1         14.7       23.1           3560  
...             ...          ...        ...            ...  
17757          75.7         65.0       79.0            145  
17758          13.5         10.8       14.0            170  
17759          21.5         12.5       22.3           3477  
17760          22.3          6.6       20.7           3792  
17761          40.6         37.6       41.3           2000  

[49303 rows x 10 columns]

In [137]:
df.to_csv("106merged.csv")

In [138]:
crop_dict = {'LA': '甘藍', 'LC': '包心白', 'LH': '菠菜', 'LI': '萵苣菜', 'LF': '蕹菜', 'LN': '油菜', 'LO': '甘藷葉', 'LJ': '芥菜', 'LL': '茼蒿', 'LG': '芹菜', 'LB': '小白菜', 'LD': '青江白菜', \
    'SO': '甘薯','SA': '蘿蔔','SB': '胡蘿蔔','SC': '馬鈴薯','SL': '豆薯', 'SE': '青蔥','SG': '大蒜', 'SD': '洋蔥', \
    'FB': '花椰菜','FR': '青花苔','FY': '玉米','FJ': '蕃茄','FF': '絲瓜','FC': '胡瓜','FD': '花胡瓜','FH2':'扁蒲-圓形','FG': '苦瓜','FT':'南瓜','FI1':'茄子-胭脂茄','FN': '敏豆','FK4': '甜椒-彩色種','FK5': '甜椒-青椒','FM': '菜豆','FP1':'萊豆-豆莢'    
}
len(crop_dict)

36

In [139]:
df.MarketCode = df.MarketCode.astype('int64')
df.dtypes

CropCode           object
CropName           object
MarketName         object
TransDate          object
MarketCode          int64
Upper_Price       float64
Middle_Price      float64
Lower_Price       float64
Avg_Price         float64
Trans_Quantity     object
dtype: object

In [140]:
# 合併兩者，df為106年，recent為其餘年份
market_list = ["台中市","高雄市"]
for key in crop_dict.keys():
    for market in market_list:
        # print(df[(df['CropCode'].str.find(key)!=-1) & (df['MarketName']==market)])
        # print(df[(df['CropCode'].str.find(key)!=-1) & (df['MarketName']==market)].dtypes)
        recent = pd.read_csv("data_new_api1_5y/"+crop_dict[key]+"_"+market+".csv",header=0,index_col=0)
        # print(crop_dict[key])
        # print(recent.dtypes)
        merged = pd.concat([df[(df['CropCode'].str.find(key)!=-1) & (df['MarketName']==market)],recent],axis=0,ignore_index=True)
        merged = merged.sort_values(['TransDate'],ascending=False)
        merged = merged.reset_index(drop=True)
        merged.to_csv("data_new_api1_merged/"+crop_dict[key]+"_"+market+".csv")

# 將兩個api結果合併

In [141]:
# df1 = pd.read_csv("data_api1_merged/胡瓜_西螺鎮.csv",index_col=0)
# df2 = pd.read_csv("data_api_5y_2/胡瓜_西螺鎮.csv",index_col=0)

In [143]:
for filename in os.listdir("data_new_api1_merged"):
    print("------"*8)
    print(filename)
    df1 = pd.read_csv("data_new_api1_merged/"+filename,index_col=0)
    df2 = pd.read_csv("data_new_api2_5y/"+filename,index_col=0)
    # df1 column 順序、作物名稱統一、休市格式, df2 rename column
    df1 = df1[['TransDate','CropCode','CropName','MarketCode','MarketName','Upper_Price','Middle_Price','Lower_Price','Avg_Price','Trans_Quantity']]
    df1['CropName'] = df1['CropName'].str.replace(' ','-',1)
    df1['CropName'] = df1['CropName'].str.rstrip()
    df1.loc[df1['CropCode']=="-","CropCode"] = "rest"
    df2 = df2.rename(columns={'交易日期':'TransDate','作物代號':'CropCode','作物名稱':'CropName','市場代號':'MarketCode','市場名稱':'MarketName','上價':'Upper_Price','中價':'Middle_Price','下價':'Lower_Price','平均價':'Avg_Price','交易量':'Trans_Quantity'})
    print(df1.describe())
    print(df2.describe())

    # outer merge
    merged = pd.merge(df1,df2,how="outer",on=['TransDate','CropCode','CropName','MarketName','MarketCode','Upper_Price','Middle_Price','Lower_Price','Avg_Price','Trans_Quantity'],indicator=True)
    merged = merged.sort_values(['TransDate'])
    merged = merged.reset_index(drop=True)
    print(merged.describe())
    merged.to_csv("data_new_final_merge/"+filename)
    

------------------------------------------------
青蔥_高雄市.csv
       MarketCode  Upper_Price  Middle_Price  Lower_Price    Avg_Price  \
count      5277.0  5277.000000   5277.000000  5277.000000  5277.000000   
mean        800.0    60.924218     53.334129    45.716752    53.329088   
std           0.0    44.506987     40.232738    36.976283    40.053383   
min         800.0     0.000000      0.000000     0.000000     0.000000   
25%         800.0    31.500000     25.400000    17.300000    25.700000   
50%         800.0    53.500000     43.000000    36.300000    43.400000   
75%         800.0    75.000000     72.300000    66.300000    72.200000   
max         800.0   247.800000    230.900000   212.200000   222.300000   

       Trans_Quantity  
count     5277.000000  
mean       934.853515  
std        926.247691  
min          0.000000  
25%        200.000000  
50%        620.000000  
75%       1480.000000  
max       5734.000000  
       MarketCode  Upper_Price  Middle_Price  Lower_Price

       MarketCode  Upper_Price  Middle_Price  Lower_Price    Avg_Price  \
count      4740.0  4740.000000   4740.000000  4740.000000  4740.000000   
mean        400.0    46.348966     39.195443    30.523038    38.356899   
std           0.0    45.155617     39.438047    32.240134    38.807940   
min         400.0     0.000000      0.000000     0.000000     0.000000   
25%         400.0    21.000000     18.000000    12.600000    18.000000   
50%         400.0    33.000000     27.500000    20.000000    26.300000   
75%         400.0    53.525000     45.000000    35.000000    42.300000   
max         400.0   319.300000    288.200000   227.000000   279.200000   

       Trans_Quantity  
count     4740.000000  
mean       667.519620  
std        919.954776  
min          0.000000  
25%         43.000000  
50%        164.000000  
75%       1030.000000  
max       4992.000000  
       MarketCode  Upper_Price  Middle_Price  Lower_Price    Avg_Price  \
count      4742.0  4742.000000   4742.00000

------------------------------------------------
蘿蔔_台中市.csv
       MarketCode  Upper_Price  Middle_Price  Lower_Price    Avg_Price  \
count      4494.0  4494.000000   4494.000000  4494.000000  4494.000000   
mean        400.0    15.615888     12.695995     9.909301    12.540031   
std           0.0    11.841782     10.336767     9.647955    10.170685   
min         400.0     0.000000      0.000000     0.000000     0.000000   
25%         400.0     8.000000      5.700000     3.200000     5.800000   
50%         400.0    14.000000     10.300000     7.000000    10.300000   
75%         400.0    20.700000     17.800000    14.700000    17.400000   
max         400.0   155.000000    155.000000   155.000000   155.000000   

       Trans_Quantity  
count     4494.000000  
mean      2344.484869  
std       3513.652891  
min          0.000000  
25%         60.000000  
50%        551.500000  
75%       3537.500000  
max      35734.000000  
       MarketCode  Upper_Price  Middle_Price  Lower_Price

       MarketCode  Upper_Price  Middle_Price  Lower_Price    Avg_Price  \
count      5608.0  5608.000000   5608.000000  5608.000000  5608.000000   
mean        400.0    23.873003     18.937981    13.996897    19.073039   
std           0.0    14.282559     11.761248    10.199133    11.722855   
min         400.0     0.000000      0.000000     0.000000     0.000000   
25%         400.0    16.300000     12.200000     7.700000    12.600000   
50%         400.0    23.000000     18.000000    12.100000    18.000000   
75%         400.0    31.200000     25.000000    19.000000    25.000000   
max         400.0   136.000000    136.000000   136.000000   136.000000   

       Trans_Quantity  
count     5608.000000  
mean      2273.396220  
std       3204.197943  
min         -1.000000  
25%         42.000000  
50%        681.500000  
75%       3686.250000  
max      26996.000000  
------------------------------------------------
芹菜_台中市.csv
       MarketCode  Upper_Price  Middle_Price  Lower_Price

       MarketCode  Upper_Price  Middle_Price  Lower_Price    Avg_Price  \
count      6198.0  6198.000000   6198.000000  6198.000000  6198.000000   
mean        800.0    24.328671     17.869990    10.995127    17.787028   
std           0.0    15.019499     11.334968     9.788134    11.184096   
min         800.0     0.000000      0.000000     0.000000     0.000000   
25%         800.0    18.000000     12.200000     5.900000    12.525000   
50%         800.0    25.000000     18.200000    10.000000    18.000000   
75%         800.0    30.900000     23.300000    15.000000    23.000000   
max         800.0   165.000000    160.000000   160.000000   160.000000   

       Trans_Quantity  
count     6198.000000  
mean      1382.636657  
std       1305.689874  
min          0.000000  
25%        158.500000  
50%       1140.500000  
75%       2330.000000  
max       8525.000000  
------------------------------------------------
青江白菜_高雄市.csv
       MarketCode  Upper_Price  Middle_Price  Lower_Pri

...

       MarketCode  Upper_Price  Middle_Price  Lower_Price    Avg_Price  \
count      3468.0  3468.000000   3468.000000  3468.000000  3468.000000   
mean        400.0    48.262601     36.397895    23.575865    36.428922   
std           0.0    32.607850     27.556060    23.199266    27.164571   
min         400.0     0.000000      0.000000     0.000000     0.000000   
25%         400.0    26.200000     16.300000     6.775000    16.800000   
50%         400.0    48.000000     32.500000    16.350000    33.200000   
75%         400.0    73.000000     55.300000    35.000000    55.925000   
max         400.0   152.000000    130.000000   125.000000   127.900000   

       Trans_Quantity  
count     3468.000000  
mean      1264.917820  
std       1776.332757  
min          0.000000  
25%         44.000000  
50%        288.000000  
75%       2081.750000  
max      11268.000000  
------------------------------------------------
蕹菜_台中市.csv
       MarketCode  Upper_Price  Middle_Price  Lower_Price

------------------------------------------------
洋蔥_高雄市.csv
       MarketCode  Upper_Price  Middle_Price  Lower_Price    Avg_Price  \
count      3397.0  3397.000000   3397.000000  3397.000000  3397.000000   
mean        800.0    22.194790     19.950662    14.623815    19.334089   
std           0.0     9.769267      9.047284     8.142258     8.820643   
min         800.0     0.000000      0.000000     0.000000     0.000000   
25%         800.0    20.900000     17.900000     9.300000    17.100000   
50%         800.0    25.200000     23.400000    16.300000    22.500000   
75%         800.0    27.500000     25.300000    20.800000    24.600000   
max         800.0    41.700000     39.400000    38.000000    38.600000   

       Trans_Quantity  
count     3397.000000  
mean      3509.749190  
std       2611.587167  
min          0.000000  
25%       1730.000000  
50%       3159.000000  
75%       5000.000000  
max      19948.000000  
       MarketCode  Upper_Price  Middle_Price  Lower_Price

       MarketCode  Upper_Price  Middle_Price  Lower_Price    Avg_Price  \
count      2291.0  2291.000000   2291.000000  2291.000000  2291.000000   
mean        800.0    52.026626     39.866216    22.727106    38.869577   
std           0.0    38.842605     32.397117    22.460290    30.947704   
min         800.0     0.000000      0.000000     0.000000     0.000000   
25%         800.0    21.850000     16.550000     8.350000    18.000000   
50%         800.0    47.000000     34.200000    17.000000    33.500000   
75%         800.0    80.750000     62.200000    30.500000    60.100000   
max         800.0   194.100000    160.300000   136.800000   157.300000   

       Trans_Quantity  
count     2291.000000  
mean      2476.467918  
std       2703.266005  
min          0.000000  
25%         45.500000  
50%       1598.000000  
75%       4158.500000  
max      14417.000000  
       MarketCode  Upper_Price  Middle_Price  Lower_Price    Avg_Price  \
count      2720.0  2720.000000   2720.00000

       MarketCode  Upper_Price  Middle_Price  Lower_Price    Avg_Price  \
count      1157.0  1157.000000   1157.000000  1157.000000  1157.000000   
mean        800.0    19.530424     16.724460    13.608038    16.663008   
std           0.0    17.675610     15.253753    13.189647    15.198422   
min         800.0     0.000000      0.000000     0.000000     0.000000   
25%         800.0     0.000000      0.000000     0.000000     0.000000   
50%         800.0    25.000000     20.900000    14.800000    20.700000   
75%         800.0    35.000000     28.800000    23.500000    28.400000   
max         800.0    78.000000     67.000000    60.000000    67.800000   

       Trans_Quantity  
count     1157.000000  
mean       281.828003  
std        323.011089  
min          0.000000  
25%          0.000000  
50%        200.000000  
75%        470.000000  
max       1850.000000  
       MarketCode  Upper_Price  Middle_Price  Lower_Price    Avg_Price  \
count      1283.0  1283.000000   1283.00000

------------------------------------------------
萊豆-豆莢_高雄市.csv
       MarketCode  Upper_Price  Middle_Price  Lower_Price    Avg_Price  \
count      1405.0  1405.000000   1405.000000  1405.000000  1405.000000   
mean        800.0    53.280569     49.970534    44.194947    49.478363   
std           0.0    46.878007     44.308719    41.305836    44.084738   
min         800.0     0.000000      0.000000     0.000000     0.000000   
25%         800.0     0.000000      0.000000     0.000000     0.000000   
50%         800.0    51.500000     49.400000    39.700000    47.900000   
75%         800.0    90.000000     84.500000    71.700000    83.900000   
max         800.0   175.000000    175.000000   175.000000   175.000000   

       Trans_Quantity  
count     1405.000000  
mean       482.745907  
std        553.669484  
min          0.000000  
25%          0.000000  
50%        267.000000  
75%        881.000000  
max       2819.000000  
       MarketCode  Upper_Price  Middle_Price  Lower_Pr

### 以下是分散版，不用跑

## 改正一些細項錯誤的CropCode e.g.'LB22','FB11','SA11'

In [160]:
file = "./data_new_final_merge/花椰菜_高雄市.csv"
temp = pd.read_csv(file, index_col=0)
# temp = temp.drop(temp[temp['CropCode']=='SA3'].index)
temp.loc[temp['CropCode']=='FB11','CropCode'] = 'FB1'
print(temp['CropCode'].value_counts())
temp.to_csv(file)

FB1     1819
rest     587
FB9      158
FB0      156
Name: CropCode, dtype: int64


In [ ]:
df2

In [ ]:
df2 = df2.rename(columns={'交易日期':'TransDate','作物代號':'CropCode','作物名稱':'CropName','市場代號':'MarketCode','市場名稱':'MarketName','上價':'Upper_Price','中價':'Middle_Price','下價':'Lower_Price','平均價':'Avg_Price','交易量':'Trans_Quantity'})
df2

In [ ]:
df1.loc[df1['CropCode']=="-","CropCode"] = "rest"

In [ ]:
df1[df1['CropCode']=="rest"]

In [ ]:
df2[df2['CropCode']=='rest']

In [ ]:
merged = pd.merge(df1,df2,how="outer",on=['TransDate','CropCode','CropName','MarketName','MarketCode','Upper_Price','Middle_Price','Lower_Price','Avg_Price','Trans_Quantity'],indicator=True)
merged = merged.sort_values(['TransDate'])
merged = merged.reset_index(drop=True)
merged

In [ ]:
merged.to_csv("test_merge.csv")

## 檢查無資料的日期

In [47]:
#106-110五年西元年月日
date_list = [d.strftime('%Y.%m.%d') for d in pd.date_range('20170101','20211231')]

In [48]:
#轉為民國年
date_list = [d.replace(d[0:4],str(int(d[0:4])-1911)) for d in date_list]
date_list

['106.01.01',
 '106.01.02',
 '106.01.03',
 '106.01.04',
 '106.01.05',
 '106.01.06',
 '106.01.07',
 '106.01.08',
 '106.01.09',
 '106.01.10',
 '106.01.11',
 '106.01.12',
 '106.01.13',
 '106.01.14',
 '106.01.15',
 '106.01.16',
 '106.01.17',
 '106.01.18',
 '106.01.19',
 '106.01.20',
 '106.01.21',
 '106.01.22',
 '106.01.23',
 '106.01.24',
 '106.01.25',
 '106.01.26',
 '106.01.27',
 '106.01.28',
 '106.01.29',
 '106.01.30',
 '106.01.31',
 '106.02.01',
 '106.02.02',
 '106.02.03',
 '106.02.04',
 '106.02.05',
 '106.02.06',
 '106.02.07',
 '106.02.08',
 '106.02.09',
 '106.02.10',
 '106.02.11',
 '106.02.12',
 '106.02.13',
 '106.02.14',
 '106.02.15',
 '106.02.16',
 '106.02.17',
 '106.02.18',
 '106.02.19',
 '106.02.20',
 '106.02.21',
 '106.02.22',
 '106.02.23',
 '106.02.24',
 '106.02.25',
 '106.02.26',
 '106.02.27',
 '106.02.28',
 '106.03.01',
 '106.03.02',
 '106.03.03',
 '106.03.04',
 '106.03.05',
 '106.03.06',
 '106.03.07',
 '106.03.08',
 '106.03.09',
 '106.03.10',
 '106.03.11',
 '106.03.12',
 '106.

In [49]:
# 五年總天數
len(date_list)

1826

## 各市場休市日期

休市日會先到 https://data.coa.gov.tw/open_search.aspx?id=I01 手動下載，放到 data_rest_date 資料夾

In [37]:
rest_market = {}
for filename in os.listdir("data_rest_date"):
    rest_date = []
    df_104 = pd.read_csv("data_rest_date/"+filename)
    for index,row in df_104.iterrows():
        if int(str(row['休市年月'])[0:3]) >= 106 and int(str(row['休市年月'])[0:3]) <= 110:
            for day in str(row['休市日']).split('、'):
                rest_date.append(str(row['休市年月'])[0:3]+"."+str(row['休市年月'])[-2:]+"."+day)
    rest_market[filename[:-4]] = rest_date
rest_market

{'台北一': ['110.12.06',
  '110.12.09',
  '110.12.13',
  '110.12.20',
  '110.12.27',
  '110.11.01',
  '110.11.08',
  '110.11.11',
  '110.11.15',
  '110.11.22',
  '110.11.29',
  '110.10.04',
  '110.10.11',
  '110.10.14',
  '110.10.18',
  '110.10.25',
  '110.09.06',
  '110.09.13',
  '110.09.16',
  '110.09.22',
  '110.09.23',
  '110.09.27',
  '110.08.02',
  '110.08.09',
  '110.08.16',
  '110.08.23',
  '110.08.24',
  '110.08.30',
  '110.07.05',
  '110.07.12',
  '110.07.15',
  '110.07.19',
  '110.07.26',
  '110.06.03',
  '110.06.07',
  '110.06.15',
  '110.06.16',
  '110.06.21',
  '110.06.28',
  '110.05.03',
  '110.05.10',
  '110.05.17',
  '110.05.24',
  '110.05.31',
  '110.04.04',
  '110.04.05',
  '110.04.12',
  '110.04.19',
  '110.04.26',
  '110.03.01',
  '110.03.08',
  '110.03.15',
  '110.03.22',
  '110.03.23',
  '110.03.29',
  '110.02.01',
  '110.02.05',
  '110.02.12',
  '110.02.13',
  '110.02.14',
  '110.02.15',
  '110.02.16',
  '110.02.20',
  '110.02.22',
  '110.02.28',
  '110.01.04',
  '

In [38]:
# 各縣市五年休市天數
for key in rest_market:
    print(key,len(rest_market[key]))

台北一 333
高雄市 312
西螺鎮 269
台中市 334
台北二 333
屏東市 334


In [44]:
for filename in os.listdir("data_new_final_merge"):
    # filename = "大蒜_屏東市.csv"
    df = pd.read_csv("data_new_final_merge/"+filename,index_col=0)
    print(df['CropCode'].value_counts())

SE5     1514
SE6     1507
SE2     1265
rest     587
SE4      308
SE3      213
SE9       32
SE1        3
Name: CropCode, dtype: int64
LD1     1491
rest     618
LD8       10
LD2        4
Name: CropCode, dtype: int64
FN1     1514
FN5     1514
rest     587
FN3      492
FN4      375
FN0        3
FN2        1
Name: CropCode, dtype: int64
LC9     2704
LC1     1818
LC3     1117
LC0      913
rest     587
LC6      495
LC5      232
Name: CropCode, dtype: int64
LO1     1793
rest     618
Name: CropCode, dtype: int64
SE6     1490
SE5     1026
SE2      966
rest     618
SE4      475
SE3      258
SE9       51
SE1        3
Name: CropCode, dtype: int64
SG6     1491
SG2     1396
SG7     1349
SG5     1338
rest     618
SG4      394
SG1      192
SG3      124
SG9       17
Name: CropCode, dtype: int64
FC1     1491
rest     618
FC2        2
Name: CropCode, dtype: int64
FB1     1487
rest     618
FB0      296
FB9       61
FB2        7
Name: CropCode, dtype: int64
FI1     872
rest    618
Name: CropCode, dtype: int

### 填補各檔案中、各細項缺少的日期 (將Price, 交易量設定為NaN)

In [ ]:
for filename in os.listdir("data_new_final_merge"):
    # filename = "大蒜_屏東市.csv"
    df = pd.read_csv("data_new_final_merge/"+filename,index_col=0)
    # df['CropName'].value_counts()""
    #列出所有種類細項
    genres = list(df['CropCode'].unique())
    genres.remove("rest")
    print(genres)
    print(filename)

    #開始找各細項日期缺值
    cnt = 0
    for gen in genres:
        for date in date_list:
            if date in rest_market[filename[-7:-4]]: #如果是休市日期
                rst = df[(df['CropCode']=="rest") & (df['TransDate']==date)]
                if not rst.empty:
                    continue
                else: #休市沒資料，需補上
                    cnt += 1
                    print("休市/"+date)
                    temp = df[df['CropCode']=="rest"].iloc[0]
                    temp_dict = {'TransDate':date, 'CropCode':"rest",'CropName':休市,'MarketCode':temp['MarketCode'],'MarketName':temp['MarketName']}
                    df = df.append(temp_dict,ignore_index=True)
            else: #不是休市日
                fil = df[(df['CropCode']==gen) & (df['TransDate']==date)]
                if not fil.empty:
                    continue
                else:  # 非休市日沒資料
                    # print(gen+"/"+date)
                    cnt += 1
                    temp = df[df['CropCode']==gen].iloc[0]
                    # print(temp)
                    temp_dict = {'TransDate':date, 'CropCode':gen,'CropName':temp['CropName'],'MarketCode':temp['MarketCode'],'MarketName':temp['MarketName']}
                    df = df.append(temp_dict,ignore_index=True)
                    # print(df[(df['CropCode']=='SG5') & (df['TransDate']=='106.08.02')])
    print(cnt)
    df = df.sort_values(['TransDate'])
    df = df.reset_index(drop=True)
    df.to_csv("data_new_filled/"+filename)
    
    ####### 檢查是否完全填滿日期 #######
    print("---"*8)
    cnt_test = 0
    for gen in genres:
        for date in date_list:
            if date in rest_market[filename[-7:-4]]:  # 如果是休市日
                rst = df[(df['CropCode']=="rest") & (df['TransDate']==date)]
                if not rst.empty:
                    continue
                else:  # 卻找不到休市資料
                    cnt_test += 1
                    print("休市/"+date)
            else:  # 如果不是休市日，要有這個細項 NaN 的資料
                fil = df[(df['CropCode']==gen) & (df['TransDate']==date)]
                if not fil.empty:
                    continue
                else:
                    cnt_test += 1
                    print(gen+"/"+date)
    if(cnt_test > 0):
        print(filename)
    print("==="*8)

['SE2', 'SE6', 'SE4', 'SE5', 'SE3', 'SE9', 'SE1']
青蔥_高雄市.csv
5768
------------------------
['LD1', 'LD8', 'LD2']
青江白菜_台中市.csv
2972
------------------------
['FN1', 'FN3', 'FN5', 'FN0', 'FN4', 'FN2']
敏豆_高雄市.csv
5185
------------------------
['LC3', 'LC6', 'LC9', 'LC1', 'LC0', 'LC5']
包心白_高雄市.csv
3702
------------------------
['LO1']
甘藷葉_台中市.csv
2
------------------------
['SE5', 'SE2', 'SE6', 'SE4', 'SE3', 'SE1', 'SE9']
青蔥_台中市.csv
6184
------------------------
['SG6', 'SG5', 'SG7', 'SG2', 'SG4', 'SG1', 'SG3', 'SG9']
大蒜_台中市.csv
5637
------------------------
['FC1', 'FC2']
胡瓜_台中市.csv
1492
------------------------
['FB1', 'FB0', 'FB2', 'FB9']
花椰菜_台中市.csv
4118
------------------------
['FI1']
茄子-胭脂茄_台中市.csv
620
------------------------
['SO0', 'SO1', 'SO3', 'SO2']
甘薯_台中市.csv
307
------------------------
['SA6', 'SA3', 'SA0', 'SA4', 'SA1', 'SA9', 'SA5', 'SA2', 'SA7']
蘿蔔_台中市.csv
9409
------------------------
['SG7', 'SG6', 'SG5', 'SG9', 'SG2', 'SG4', 'SG3', 'SG1']
大蒜_高雄市.csv
5405
-------------

In [10]:
#檢查是否完全填滿日期
# for filename in os.listdir("data_filled"):
#     df = pd.read_csv("data_filled/"+filename,index_col=0)
#     genres = list(df['CropCode'].unique())
#     genres.remove("rest")
# #     print(genres)
    
#     cnt_test = 0
#     for gen in genres:
#         for date in date_list:
#             if date in rest_market[filename[-7:-4]]:
#                 rst = df[(df['CropCode']=="rest") & (df['TransDate']==date)]
#                 if not rst.empty:
#                     continue
#                 else:
#                     cnt_test += 1
#                     print("休市/"+date)
#             else:
#                 fil = df[(df['CropCode']==gen) & (df['TransDate']==date)]
#                 if not fil.empty:
#                     continue
#                 else:
#                     cnt_test += 1
#                     print(gen+"/"+date)
#     if(cnt_test > 0):
#         print(filename)
#     print("==="*8)


SE6/2017.01.01
SE6/2017.01.02
SE6/2017.01.03
SE6/2017.01.04
SE6/2017.01.05
SE6/2017.01.06
SE6/2017.01.07
SE6/2017.01.08
SE6/2017.01.09
SE6/2017.01.10
SE6/2017.01.11
SE6/2017.01.12
SE6/2017.01.13
SE6/2017.01.14
SE6/2017.01.15
SE6/2017.01.16
SE6/2017.01.17
SE6/2017.01.18
SE6/2017.01.19
SE6/2017.01.20
SE6/2017.01.21
SE6/2017.01.22
SE6/2017.01.23
SE6/2017.01.24
SE6/2017.01.25
SE6/2017.01.26
SE6/2017.01.27
SE6/2017.01.28
SE6/2017.01.29
SE6/2017.01.30
SE6/2017.01.31
SE6/2017.02.01
SE6/2017.02.02
SE6/2017.02.03
SE6/2017.02.04
SE6/2017.02.05
SE6/2017.02.06
SE6/2017.02.07
SE6/2017.02.08
SE6/2017.02.09
SE6/2017.02.10
SE6/2017.02.11
SE6/2017.02.12
SE6/2017.02.13
SE6/2017.02.14
SE6/2017.02.15
SE6/2017.02.16
SE6/2017.02.17
SE6/2017.02.18
SE6/2017.02.19
SE6/2017.02.20
SE6/2017.02.21
SE6/2017.02.22
SE6/2017.02.23
SE6/2017.02.24
SE6/2017.02.25
SE6/2017.02.26
SE6/2017.02.27
SE6/2017.02.28
SE6/2017.03.01
SE6/2017.03.02
SE6/2017.03.03
SE6/2017.03.04
SE6/2017.03.05
SE6/2017.03.06
SE6/2017.03.07
SE6/2017.0

SE6/2018.07.30
SE6/2018.07.31
SE6/2018.08.01
SE6/2018.08.02
SE6/2018.08.03
SE6/2018.08.04
SE6/2018.08.05
SE6/2018.08.06
SE6/2018.08.07
SE6/2018.08.08
SE6/2018.08.09
SE6/2018.08.10
SE6/2018.08.11
SE6/2018.08.12
SE6/2018.08.13
SE6/2018.08.14
SE6/2018.08.15
SE6/2018.08.16
SE6/2018.08.17
SE6/2018.08.18
SE6/2018.08.19
SE6/2018.08.20
SE6/2018.08.21
SE6/2018.08.22
SE6/2018.08.23
SE6/2018.08.24
SE6/2018.08.25
SE6/2018.08.26
SE6/2018.08.27
SE6/2018.08.28
SE6/2018.08.29
SE6/2018.08.30
SE6/2018.08.31
SE6/2018.09.01
SE6/2018.09.02
SE6/2018.09.03
SE6/2018.09.04
SE6/2018.09.05
SE6/2018.09.06
SE6/2018.09.07
SE6/2018.09.08
SE6/2018.09.09
SE6/2018.09.10
SE6/2018.09.11
SE6/2018.09.12
SE6/2018.09.13
SE6/2018.09.14
SE6/2018.09.15
SE6/2018.09.16
SE6/2018.09.17
SE6/2018.09.18
SE6/2018.09.19
SE6/2018.09.20
SE6/2018.09.21
SE6/2018.09.22
SE6/2018.09.23
SE6/2018.09.24
SE6/2018.09.25
SE6/2018.09.26
SE6/2018.09.27
SE6/2018.09.28
SE6/2018.09.29
SE6/2018.09.30
SE6/2018.10.01
SE6/2018.10.02
SE6/2018.10.03
SE6/2018.1

SE6/2020.03.11
SE6/2020.03.12
SE6/2020.03.13
SE6/2020.03.14
SE6/2020.03.15
SE6/2020.03.16
SE6/2020.03.17
SE6/2020.03.18
SE6/2020.03.19
SE6/2020.03.20
SE6/2020.03.21
SE6/2020.03.22
SE6/2020.03.23
SE6/2020.03.24
SE6/2020.03.25
SE6/2020.03.26
SE6/2020.03.27
SE6/2020.03.28
SE6/2020.03.29
SE6/2020.03.30
SE6/2020.03.31
SE6/2020.04.01
SE6/2020.04.02
SE6/2020.04.03
SE6/2020.04.04
SE6/2020.04.05
SE6/2020.04.06
SE6/2020.04.07
SE6/2020.04.08
SE6/2020.04.09
SE6/2020.04.10
SE6/2020.04.11
SE6/2020.04.12
SE6/2020.04.13
SE6/2020.04.14
SE6/2020.04.15
SE6/2020.04.16
SE6/2020.04.17
SE6/2020.04.18
SE6/2020.04.19
SE6/2020.04.20
SE6/2020.04.21
SE6/2020.04.22
SE6/2020.04.23
SE6/2020.04.24
SE6/2020.04.25
SE6/2020.04.26
SE6/2020.04.27
SE6/2020.04.28
SE6/2020.04.29
SE6/2020.04.30
SE6/2020.05.01
SE6/2020.05.02
SE6/2020.05.03
SE6/2020.05.04
SE6/2020.05.05
SE6/2020.05.06
SE6/2020.05.07
SE6/2020.05.08
SE6/2020.05.09
SE6/2020.05.10
SE6/2020.05.11
SE6/2020.05.12
SE6/2020.05.13
SE6/2020.05.14
SE6/2020.05.15
SE6/2020.0

SE6/2021.09.20
SE6/2021.09.21
SE6/2021.09.22
SE6/2021.09.23
SE6/2021.09.24
SE6/2021.09.25
SE6/2021.09.26
SE6/2021.09.27
SE6/2021.09.28
SE6/2021.09.29
SE6/2021.09.30
SE6/2021.10.01
SE6/2021.10.02
SE6/2021.10.03
SE6/2021.10.04
SE6/2021.10.05
SE6/2021.10.06
SE6/2021.10.07
SE6/2021.10.08
SE6/2021.10.09
SE6/2021.10.10
SE6/2021.10.11
SE6/2021.10.12
SE6/2021.10.13
SE6/2021.10.14
SE6/2021.10.15
SE6/2021.10.16
SE6/2021.10.17
SE6/2021.10.18
SE6/2021.10.19
SE6/2021.10.20
SE6/2021.10.21
SE6/2021.10.22
SE6/2021.10.23
SE6/2021.10.24
SE6/2021.10.25
SE6/2021.10.26
SE6/2021.10.27
SE6/2021.10.28
SE6/2021.10.29
SE6/2021.10.30
SE6/2021.10.31
SE6/2021.11.01
SE6/2021.11.02
SE6/2021.11.03
SE6/2021.11.04
SE6/2021.11.05
SE6/2021.11.06
SE6/2021.11.07
SE6/2021.11.08
SE6/2021.11.09
SE6/2021.11.10
SE6/2021.11.11
SE6/2021.11.12
SE6/2021.11.13
SE6/2021.11.14
SE6/2021.11.15
SE6/2021.11.16
SE6/2021.11.17
SE6/2021.11.18
SE6/2021.11.19
SE6/2021.11.20
SE6/2021.11.21
SE6/2021.11.22
SE6/2021.11.23
SE6/2021.11.24
SE6/2021.1

SE2/2018.03.29
SE2/2018.03.30
SE2/2018.03.31
SE2/2018.04.01
SE2/2018.04.02
SE2/2018.04.03
SE2/2018.04.04
SE2/2018.04.05
SE2/2018.04.06
SE2/2018.04.07
SE2/2018.04.08
SE2/2018.04.09
SE2/2018.04.10
SE2/2018.04.11
SE2/2018.04.12
SE2/2018.04.13
SE2/2018.04.14
SE2/2018.04.15
SE2/2018.04.16
SE2/2018.04.17
SE2/2018.04.18
SE2/2018.04.19
SE2/2018.04.20
SE2/2018.04.21
SE2/2018.04.22
SE2/2018.04.23
SE2/2018.04.24
SE2/2018.04.25
SE2/2018.04.26
SE2/2018.04.27
SE2/2018.04.28
SE2/2018.04.29
SE2/2018.04.30
SE2/2018.05.01
SE2/2018.05.02
SE2/2018.05.03
SE2/2018.05.04
SE2/2018.05.05
SE2/2018.05.06
SE2/2018.05.07
SE2/2018.05.08
SE2/2018.05.09
SE2/2018.05.10
SE2/2018.05.11
SE2/2018.05.12
SE2/2018.05.13
SE2/2018.05.14
SE2/2018.05.15
SE2/2018.05.16
SE2/2018.05.17
SE2/2018.05.18
SE2/2018.05.19
SE2/2018.05.20
SE2/2018.05.21
SE2/2018.05.22
SE2/2018.05.23
SE2/2018.05.24
SE2/2018.05.25
SE2/2018.05.26
SE2/2018.05.27
SE2/2018.05.28
SE2/2018.05.29
SE2/2018.05.30
SE2/2018.05.31
SE2/2018.06.01
SE2/2018.06.02
SE2/2018.0

...

SA32/2021.09.28
SA32/2021.09.29
SA32/2021.09.30
SA32/2021.10.01
SA32/2021.10.02
SA32/2021.10.03
SA32/2021.10.04
SA32/2021.10.05
SA32/2021.10.06
SA32/2021.10.07
SA32/2021.10.08
SA32/2021.10.09
SA32/2021.10.10
SA32/2021.10.11
SA32/2021.10.12
SA32/2021.10.13
SA32/2021.10.14
SA32/2021.10.15
SA32/2021.10.16
SA32/2021.10.17
SA32/2021.10.18
SA32/2021.10.19
SA32/2021.10.20
SA32/2021.10.21
SA32/2021.10.22
SA32/2021.10.23
SA32/2021.10.24
SA32/2021.10.25
SA32/2021.10.26
SA32/2021.10.27
SA32/2021.10.28
SA32/2021.10.29
SA32/2021.10.30
SA32/2021.10.31
SA32/2021.11.01
SA32/2021.11.02
SA32/2021.11.03
SA32/2021.11.04
SA32/2021.11.05
SA32/2021.11.06
SA32/2021.11.07
SA32/2021.11.08
SA32/2021.11.09
SA32/2021.11.10
SA32/2021.11.11
SA32/2021.11.12
SA32/2021.11.13
SA32/2021.11.14
SA32/2021.11.15
SA32/2021.11.16
SA32/2021.11.17
SA32/2021.11.18
SA32/2021.11.19
SA32/2021.11.20
SA32/2021.11.21
SA32/2021.11.22
SA32/2021.11.23
SA32/2021.11.24
SA32/2021.11.25
SA32/2021.11.26
SA32/2021.11.27
SA32/2021.11.28
SA32/202

SA22/2018.06.28
SA22/2018.06.29
SA22/2018.06.30
SA22/2018.07.01
SA22/2018.07.02
SA22/2018.07.03
SA22/2018.07.04
SA22/2018.07.05
SA22/2018.07.06
SA22/2018.07.07
SA22/2018.07.08
SA22/2018.07.09
SA22/2018.07.10
SA22/2018.07.11
SA22/2018.07.12
SA22/2018.07.13
SA22/2018.07.14
SA22/2018.07.15
SA22/2018.07.16
SA22/2018.07.17
SA22/2018.07.18
SA22/2018.07.19
SA22/2018.07.20
SA22/2018.07.21
SA22/2018.07.22
SA22/2018.07.23
SA22/2018.07.24
SA22/2018.07.25
SA22/2018.07.26
SA22/2018.07.27
SA22/2018.07.28
SA22/2018.07.29
SA22/2018.07.30
SA22/2018.07.31
SA22/2018.08.01
SA22/2018.08.02
SA22/2018.08.03
SA22/2018.08.04
SA22/2018.08.05
SA22/2018.08.06
SA22/2018.08.07
SA22/2018.08.08
SA22/2018.08.09
SA22/2018.08.10
SA22/2018.08.11
SA22/2018.08.12
SA22/2018.08.13
SA22/2018.08.14
SA22/2018.08.15
SA22/2018.08.16
SA22/2018.08.17
SA22/2018.08.18
SA22/2018.08.19
SA22/2018.08.20
SA22/2018.08.21
SA22/2018.08.22
SA22/2018.08.23
SA22/2018.08.24
SA22/2018.08.25
SA22/2018.08.26
SA22/2018.08.27
SA22/2018.08.28
SA22/201

SA22/2020.03.28
SA22/2020.03.29
SA22/2020.03.30
SA22/2020.03.31
SA22/2020.04.01
SA22/2020.04.02
SA22/2020.04.03
SA22/2020.04.04
SA22/2020.04.05
SA22/2020.04.06
SA22/2020.04.07
SA22/2020.04.08
SA22/2020.04.09
SA22/2020.04.10
SA22/2020.04.11
SA22/2020.04.12
SA22/2020.04.13
SA22/2020.04.14
SA22/2020.04.15
SA22/2020.04.16
SA22/2020.04.17
SA22/2020.04.18
SA22/2020.04.19
SA22/2020.04.20
SA22/2020.04.21
SA22/2020.04.22
SA22/2020.04.23
SA22/2020.04.24
SA22/2020.04.25
SA22/2020.04.26
SA22/2020.04.27
SA22/2020.04.28
SA22/2020.04.29
SA22/2020.04.30
SA22/2020.05.01
SA22/2020.05.02
SA22/2020.05.03
SA22/2020.05.04
SA22/2020.05.05
SA22/2020.05.06
SA22/2020.05.07
SA22/2020.05.08
SA22/2020.05.09
SA22/2020.05.10
SA22/2020.05.11
SA22/2020.05.12
SA22/2020.05.13
SA22/2020.05.14
SA22/2020.05.15
SA22/2020.05.16
SA22/2020.05.17
SA22/2020.05.18
SA22/2020.05.19
SA22/2020.05.20
SA22/2020.05.21
SA22/2020.05.22
SA22/2020.05.23
SA22/2020.05.24
SA22/2020.05.25
SA22/2020.05.26
SA22/2020.05.27
SA22/2020.05.28
SA22/202

SA22/2021.11.30
SA22/2021.12.01
SA22/2021.12.02
SA22/2021.12.03
SA22/2021.12.04
SA22/2021.12.05
SA22/2021.12.06
SA22/2021.12.07
SA22/2021.12.08
SA22/2021.12.09
SA22/2021.12.10
SA22/2021.12.11
SA22/2021.12.12
SA22/2021.12.13
SA22/2021.12.14
SA22/2021.12.15
SA22/2021.12.16
SA22/2021.12.17
SA22/2021.12.18
SA22/2021.12.19
SA22/2021.12.20
SA22/2021.12.21
SA22/2021.12.22
SA22/2021.12.23
SA22/2021.12.24
SA22/2021.12.25
SA22/2021.12.26
SA22/2021.12.27
SA22/2021.12.28
SA22/2021.12.29
SA22/2021.12.30
SA22/2021.12.31
SA7/2017.01.01
SA7/2017.01.02
SA7/2017.01.03
SA7/2017.01.04
SA7/2017.01.05
SA7/2017.01.06
SA7/2017.01.07
SA7/2017.01.08
SA7/2017.01.09
SA7/2017.01.10
SA7/2017.01.11
SA7/2017.01.12
SA7/2017.01.13
SA7/2017.01.14
SA7/2017.01.15
SA7/2017.01.16
SA7/2017.01.17
SA7/2017.01.18
SA7/2017.01.19
SA7/2017.01.20
SA7/2017.01.21
SA7/2017.01.22
SA7/2017.01.23
SA7/2017.01.24
SA7/2017.01.25
SA7/2017.01.26
SA7/2017.01.27
SA7/2017.01.28
SA7/2017.01.29
SA7/2017.01.30
SA7/2017.01.31
SA7/2017.02.01
SA7/2017

KeyboardInterrupt: 

### 處理兩邊都有data/休市卻有資料

In [36]:
for filename in os.listdir("data_new_filled"):
#     if filename[:2]=="蕃茄":
    df = pd.read_csv("data_new_filled/"+filename,index_col=0)
#     genres = list(df['CropCode'].unique())
#     genres.remove("rest")
#     print(genres)

    #去除日期+細項重複，即left_only, right_only都有data且兩者不同，保留第一個出現的row
    df.drop_duplicates(subset=['TransDate','CropCode'],inplace=True)
    for date in date_list:
        if date in rest_market[filename[-7:-4]]: #表定休市日
            rst = df[df['TransDate']==date]
            if len(rst) > 1: #該休市的日期卻有其他作物資料
                df.drop(df.loc[(df['TransDate']==date) & (df['CropCode']!='rest')].index, inplace=True)
    df.to_csv("Final/"+filename)
    print(df['CropCode'].value_counts())
    print(df[df['CropCode']=='rest'])
    print(filename)


SE5     3340
SE6     3333
SE2     3091
SE4     2134
SE3     2039
SE9     1846
SE1     1829
rest     587
Name: CropCode, dtype: int64
      TransDate CropCode CropName  MarketCode MarketName  Upper_Price  \
0     106.01.01     rest       休市         800        高雄市          0.0   
5     106.01.02     rest       休市         800        高雄市          0.0   
22    106.01.07     rest       休市         800        高雄市          0.0   
30    106.01.09     rest       休市         800        高雄市          0.0   
49    106.01.15     rest       休市         800        高雄市          0.0   
...         ...      ...      ...         ...        ...          ...   
5391  110.12.19     rest       休市         800        高雄市          0.0   
5396  110.12.20     rest       休市         800        高雄市          0.0   
5408  110.12.25     rest       休市         800        高雄市          0.0   
5412  110.12.26     rest       休市         800        高雄市          0.0   
5416  110.12.27     rest       休市         800        高雄市        

FB1     1493
FB9     1492
FB2     1492
FB0     1492
rest     618
Name: CropCode, dtype: int64
      TransDate CropCode CropName  MarketCode MarketName  Upper_Price  \
0     106.01.01     rest       休市         400        台中市          0.0   
5     106.01.02     rest       休市         400        台中市          0.0   
25    106.01.07     rest       休市         400        台中市          0.0   
31    106.01.09     rest       休市         400        台中市          0.0   
48    106.01.14     rest       休市         400        台中市          0.0   
...         ...      ...      ...         ...        ...          ...   
6541  110.12.19     rest       休市         400        台中市          0.0   
6543  110.12.20     rest       休市         400        台中市          0.0   
6561  110.12.25     rest       休市         400        台中市          0.0   
6569  110.12.26     rest       休市         400        台中市          0.0   
6570  110.12.27     rest       休市         400        台中市          0.0   

      Middle_Price  Lower_Pri

       TransDate CropCode CropName  MarketCode MarketName  Upper_Price  \
3      106.01.01     rest       休市         400        台中市          0.0   
8      106.01.02     rest       休市         400        台中市          0.0   
37     106.01.07     rest       休市         400        台中市          0.0   
52     106.01.09     rest       休市         400        台中市          0.0   
82     106.01.14     rest       休市         400        台中市          0.0   
...          ...      ...      ...         ...        ...          ...   
10984  110.12.19     rest       休市         400        台中市          0.0   
10989  110.12.20     rest       休市         400        台中市          0.0   
11021  110.12.25     rest       休市         400        台中市          0.0   
11031  110.12.26     rest       休市         400        台中市          0.0   
11034  110.12.27     rest       休市         400        台中市          0.0   

       Middle_Price  Lower_Price  Avg_Price  Trans_Quantity      _merge  
3               0.0          0.0     

LA3     1514
LA6     1514
LA2     1514
LA9     1514
LA7     1514
LA4     1514
LA0     1514
LA5     1514
LA1     1514
rest     587
Name: CropCode, dtype: int64
       TransDate CropCode CropName  MarketCode MarketName  Upper_Price  \
4      106.01.01     rest       休市         800        高雄市          0.0   
10     106.01.02     rest       休市         800        高雄市          0.0   
47     106.01.07     rest       休市         800        高雄市          0.0   
66     106.01.09     rest       休市         800        高雄市          0.0   
115    106.01.15     rest       休市         800        高雄市          0.0   
...          ...      ...      ...         ...        ...          ...   
14126  110.12.19     rest       休市         800        高雄市          0.0   
14130  110.12.20     rest       休市         800        高雄市          0.0   
14171  110.12.25     rest       休市         800        高雄市          0.0   
14184  110.12.26     rest       休市         800        高雄市          0.0   
14187  110.12.27     rest  

LH3     1514
LH9     1514
LH1     1514
LH2     1514
rest     587
Name: CropCode, dtype: int64
      TransDate CropCode CropName  MarketCode MarketName  Upper_Price  \
0     106.01.01     rest       休市         800        高雄市          0.0   
5     106.01.02     rest       休市         800        高雄市          0.0   
26    106.01.07     rest       休市         800        高雄市          0.0   
31    106.01.09     rest       休市         800        高雄市          0.0   
55    106.01.15     rest       休市         800        高雄市          0.0   
...         ...      ...      ...         ...        ...          ...   
6599  110.12.19     rest       休市         800        高雄市          0.0   
6601  110.12.20     rest       休市         800        高雄市          0.0   
6618  110.12.25     rest       休市         800        高雄市          0.0   
6627  110.12.26     rest       休市         800        高雄市          0.0   
6628  110.12.27     rest       休市         800        高雄市          0.0   

      Middle_Price  Lower_Pri

LB2     1493
LB1     1493
LB3     1492
LB0     1492
LB8     1492
rest     618
Name: CropCode, dtype: int64
      TransDate CropCode CropName  MarketCode MarketName  Upper_Price  \
0     106.01.01     rest       休市         400        台中市          0.0   
6     106.01.02     rest       休市         400        台中市          0.0   
31    106.01.07     rest       休市         400        台中市          0.0   
38    106.01.09     rest       休市         400        台中市          0.0   
60    106.01.14     rest       休市         400        台中市          0.0   
...         ...      ...      ...         ...        ...          ...   
8025  110.12.19     rest       休市         400        台中市          0.0   
8026  110.12.20     rest       休市         400        台中市          0.0   
8050  110.12.25     rest       休市         400        台中市          0.0   
8055  110.12.26     rest       休市         400        台中市          0.0   
8059  110.12.27     rest       休市         400        台中市          0.0   

      Middle_Pri

FD0     1514
FD1     1514
rest     587
Name: CropCode, dtype: int64
      TransDate CropCode CropName  MarketCode MarketName  Upper_Price  \
0     106.01.01     rest       休市         800        高雄市          0.0   
4     106.01.02     rest       休市         800        高雄市          0.0   
18    106.01.07     rest       休市         800        高雄市          0.0   
24    106.01.09     rest       休市         800        高雄市          0.0   
41    106.01.15     rest       休市         800        高雄市          0.0   
...         ...      ...      ...         ...        ...          ...   
3894  110.12.19     rest       休市         800        高雄市          0.0   
3895  110.12.20     rest       休市         800        高雄市          0.0   
3906  110.12.25     rest       休市         800        高雄市          0.0   
3908  110.12.26     rest       休市         800        高雄市          0.0   
3910  110.12.27     rest       休市         800        高雄市          0.0   

      Middle_Price  Lower_Price  Avg_Price  Trans_Quant

LG8     1514
LG5     1514
LG3     1514
LG1     1514
LG9     1514
LG2     1514
LG4     1514
rest     587
Name: CropCode, dtype: int64
       TransDate CropCode CropName  MarketCode MarketName  Upper_Price  \
3      106.01.01     rest       休市         800        高雄市          0.0   
8      106.01.02     rest       休市         800        高雄市          0.0   
39     106.01.07     rest       休市         800        高雄市          0.0   
52     106.01.09     rest       休市         800        高雄市          0.0   
94     106.01.15     rest       休市         800        高雄市          0.0   
...          ...      ...      ...         ...        ...          ...   
11105  110.12.19     rest       休市         800        高雄市          0.0   
11113  110.12.20     rest       休市         800        高雄市          0.0   
11148  110.12.25     rest       休市         800        高雄市          0.0   
11154  110.12.26     rest       休市         800        高雄市          0.0   
11158  110.12.27     rest       休市         800       

FY0     1514
FY9     1514
FY4     1514
FY5     1514
FY3     1514
FY2     1514
FY1     1514
FY7     1514
FY6     1514
rest     587
Name: CropCode, dtype: int64
       TransDate CropCode CropName  MarketCode MarketName  Upper_Price  \
3      106.01.01     rest       休市         800        高雄市          0.0   
12     106.01.02     rest       休市         800        高雄市          0.0   
59     106.01.07     rest       休市         800        高雄市          0.0   
80     106.01.09     rest       休市         800        高雄市          0.0   
141    106.01.15     rest       休市         800        高雄市          0.0   
...          ...      ...      ...         ...        ...          ...   
14648  110.12.19     rest       休市         800        高雄市          0.0   
14651  110.12.20     rest       休市         800        高雄市          0.0   
14688  110.12.25     rest       休市         800        高雄市          0.0   
14703  110.12.26     rest       休市         800        高雄市          0.0   
14708  110.12.27     rest  

FY026    1515
FT5      1514
FT3      1514
FT2      1514
FT4      1514
FT6      1514
FT1      1514
FT9      1514
FT0      1514
FT7      1514
rest      587
Name: CropCode, dtype: int64
       TransDate CropCode CropName  MarketCode MarketName  Upper_Price  \
0      106.01.01     rest       休市         800        高雄市          0.0   
11     106.01.02     rest       休市         800        高雄市          0.0   
61     106.01.07     rest       休市         800        高雄市          0.0   
73     106.01.09     rest       休市         800        高雄市          0.0   
128    106.01.15     rest       休市         800        高雄市          0.0   
...          ...      ...      ...         ...        ...          ...   
15624  110.12.19     rest       休市         800        高雄市          0.0   
15627  110.12.20     rest       休市         800        高雄市          0.0   
15673  110.12.25     rest       休市         800        高雄市          0.0   
15683  110.12.26     rest       休市         800        高雄市          0.0   
156

### 去除 rest 不在休市日列表的

In [16]:
for filename in os.listdir("Final"):
    if filename[-7:]=="台中市.csv" or filename[-7:]=="高雄市.csv":
        df = pd.read_csv("Final/"+filename,index_col=0)

        for date in date_list:
            if date not in rest_market[filename[-7:-4]]: # 不是表定休市日
                rst = df[(df['TransDate']==date) & (df['CropCode']=="rest")]
                if not rst.empty: # 不是表定休市卻有 rest 資料
                    df.drop(df.loc[(df['TransDate']==date) & (df['CropCode']=='rest')].index, inplace=True)
                    print(filename)
        df.to_csv("Final/"+filename)

In [18]:
# 檢查有效天數、休市天數是否全部一致了
for filename in os.listdir("./Final"):
    if (filename[-7:]=="台中市.csv" or filename[-7:]=="高雄市.csv") and filename[:2]=="蕃茄":
        df1 = pd.read_csv("./Final/"+filename,index_col=0)
#         print(df1['CropCode'].value_counts())
        cnt_dict = df1['CropCode'].value_counts()
        print(cnt_dict)
        if filename[-7:]=="台中市.csv":
            for cnt in cnt_dict:
                if cnt != 1492 and cnt != 334:
                    print(filename)
        if filename[-7:]=="高雄市.csv":
            for cnt in cnt_dict:
                if cnt != 1514 and cnt != 312:
                    print(filename)

FJ2     1514
FJ3     1514
FJ0     1514
FJ1     1514
rest     587
Name: CropCode, dtype: int64
蕃茄_高雄市.csv
FJ3     1493
FJ2     1492
FJ0     1492
FJ1     1492
rest     618
Name: CropCode, dtype: int64
蕃茄_台中市.csv
蕃茄_台中市.csv


除去休市資料，屏東市共1492天，西螺鎮共1557天，台北二共1493天，台北一共1493天
台中市共1492，高雄市共1514

### 去除蕃茄混到小番茄

In [24]:
for filename in os.listdir("./Final"):
    if filename[:2]=="蕃茄":
        df = pd.read_csv("./Final/"+filename,index_col=0)
        print(filename)
        df.drop(df.loc[(df['CropCode'].str[:2]!='FJ') & (df['CropCode']!='rest')].index, inplace=True)
        print(df['CropCode'].value_counts())
        df.to_csv("Final/"+filename)

蕃茄_台北一.csv
FJ2    1493
FJ3    1493
FJ0    1493
FJ1    1493
Name: CropCode, dtype: int64
蕃茄_台北二.csv
FJ2    1493
FJ3    1493
FJ0    1493
FJ1    1493
Name: CropCode, dtype: int64
蕃茄_高雄市.csv
FJ2     1514
FJ3     1514
FJ0     1514
FJ1     1514
rest     587
Name: CropCode, dtype: int64
蕃茄_台中市.csv
FJ3     1493
FJ2     1492
FJ0     1492
FJ1     1492
rest     618
Name: CropCode, dtype: int64
蕃茄_屏東市.csv
FJ2    1492
FJ3    1492
FJ0    1492
FJ1    1492
Name: CropCode, dtype: int64
蕃茄_西螺鎮.csv
FJ3    1557
FJ1    1557
Name: CropCode, dtype: int64


In [ ]:
for filename in os.listdir("./Final"):
    if filename[:2]=="蕃茄":
        df = pd.read_csv("./Final/"+filename,index_col=0)
        df.drop(df.loc[df['CropCode'].str[:2]!='FJ'].index, inplace=True)
        print(df['CropCode'].value_counts())
        df.to_csv("Final/"+filename)

# 只是一些測試

In [139]:
dff = pd.read_csv("Final/苦瓜_台北一.csv",index_col=0)
dff

TransDate CropCode CropName  MarketCode MarketName  Upper_Price  \
0     106.01.01      FG0    苦瓜-其他         109        台北一         34.3   
1     106.01.01      FG9    苦瓜-進口         109        台北一          NaN   
2     106.01.01      FG3   苦瓜-山苦瓜         109        台北一         73.3   
3     106.01.01      FG2   苦瓜-青大米         109        台北一          NaN   
4     106.01.01      FG4    苦瓜-翠綠         109        台北一         58.2   
...         ...      ...      ...         ...        ...          ...   
9287  110.12.31      FG3   苦瓜-山苦瓜         109        台北一         32.0   
9288  110.12.31      FG1   苦瓜-白大米         109        台北一         64.6   
9289  110.12.31      FG0    苦瓜-其他         109        台北一         96.7   
9290  110.12.31      FG4    苦瓜-翠綠         109        台北一         82.6   
9291  110.12.31      FG9    苦瓜-進口         109        台北一          NaN   

      Middle_Price  Lower_Price  Avg_Price  Trans_Quantity _merge  
0             26.1         20.8       26.7          5813.0   both  
1              NaN          NaN        NaN             NaN    NaN  
2             55.0         55.0       58.7            41.0   both  
3              NaN          NaN        NaN             NaN    NaN  
4             44.1         26.9       43.5           718.0   both  
...            ...          ...        ...             ...    ...  
9287          32.0         32.0       32.0            11.0   both  
9288          38.6         25.4       41.1          6599.0   both  
9289          69.3         41.4       69.2          1310.0   both  
9290          44.5         23.4       47.9           366.0   both  
9291           NaN          NaN        NaN             NaN    NaN  

[9292 rows x 11 columns]

In [152]:
a = dff[dff['CropCode']=='FG2']
a
# a['Upper_Price'].notnull().sum()

TransDate CropCode CropName  MarketCode MarketName  Upper_Price  \
3     106.01.01      FG2   苦瓜-青大米         109        台北一          NaN   
11    106.01.03      FG2   苦瓜-青大米         109        台北一         27.0   
15    106.01.04      FG2   苦瓜-青大米         109        台北一          NaN   
22    106.01.05      FG2   苦瓜-青大米         109        台北一          NaN   
26    106.01.06      FG2   苦瓜-青大米         109        台北一          NaN   
...         ...      ...      ...         ...        ...          ...   
9261  110.12.26      FG2   苦瓜-青大米         109        台北一          NaN   
9273  110.12.28      FG2   苦瓜-青大米         109        台北一          NaN   
9278  110.12.29      FG2   苦瓜-青大米         109        台北一          NaN   
9285  110.12.30      FG2   苦瓜-青大米         109        台北一          NaN   
9286  110.12.31      FG2   苦瓜-青大米         109        台北一          NaN   

      Middle_Price  Lower_Price  Avg_Price  Trans_Quantity _merge  
3              NaN          NaN        NaN             NaN    NaN  
11            27.0         27.0       27.0             9.0   both  
15             NaN          NaN        NaN             NaN    NaN  
22             NaN          NaN        NaN             NaN    NaN  
26             NaN          NaN        NaN             NaN    NaN  
...            ...          ...        ...             ...    ...  
9261           NaN          NaN        NaN             NaN    NaN  
9273           NaN          NaN        NaN             NaN    NaN  
9278           NaN          NaN        NaN             NaN    NaN  
9285           NaN          NaN        NaN             NaN    NaN  
9286           NaN          NaN        NaN             NaN    NaN  

[1493 rows x 11 columns]

In [120]:
dff[dff['CropCode']=='LC1']

TransDate CropCode CropName  MarketCode MarketName  Upper_Price  \
0     106.01.01      LC1   包心白-包白         648        西螺鎮          6.5   
2     106.01.02      LC1  包心白菜-包白         648        西螺鎮          6.5   
4     106.01.03      LC1  包心白菜-包白         648        西螺鎮          6.2   
6     106.01.04      LC1   包心白-包白         648        西螺鎮          6.2   
7     106.01.05      LC1   包心白-包白         648        西螺鎮          6.2   
...         ...      ...      ...         ...        ...          ...   
2101  110.12.27      LC1  包心白菜-包白         648        西螺鎮         15.0   
2102  110.12.28      LC1  包心白菜-包白         648        西螺鎮         15.0   
2103  110.12.29      LC1  包心白菜-包白         648        西螺鎮         13.7   
2104  110.12.30      LC1  包心白菜-包白         648        西螺鎮         12.5   
2105  110.12.31      LC1  包心白菜-包白         648        西螺鎮         12.5   

      Middle_Price  Lower_Price  Avg_Price  Trans_Quantity      _merge  
0              5.0          3.0        4.9          7240.0   left_only  
2              5.0          3.0        4.9        108520.0  right_only  
4              5.0          3.0        4.8        101634.0  right_only  
6              5.0          3.0        4.8        107804.0   left_only  
7              5.0          3.0        4.8        104474.0   left_only  
...            ...          ...        ...             ...         ...  
2101          11.1          5.0       10.7         59984.0        both  
2102          11.0          5.0       10.7         51824.0        both  
2103          10.0          5.0        9.8         63952.0        both  
2104          10.0          5.0        9.5         51252.0        both  
2105          10.0          5.0        9.5         59120.0  right_only  

[1557 rows x 11 columns]

In [29]:
dff[dff['CropCode']=='SG4']

TransDate CropCode CropName  MarketCode MarketName  Upper_Price  \
1      106.01.01      SG4    大蒜-蔥蒜         900        屏東市          NaN   
14     106.01.03      SG4    大蒜-蔥蒜         900        屏東市          NaN   
21     106.01.04      SG4    大蒜-蔥蒜         900        屏東市          NaN   
26     106.01.05      SG4    大蒜-蔥蒜         900        屏東市          NaN   
34     106.01.06      SG4    大蒜-蔥蒜         900        屏東市          NaN   
...          ...      ...      ...         ...        ...          ...   
10747  110.12.26      SG4    大蒜-蔥蒜         900        屏東市          NaN   
10756  110.12.28      SG4    大蒜-蔥蒜         900        屏東市        141.8   
10765  110.12.29      SG4    大蒜-蔥蒜         900        屏東市          NaN   
10767  110.12.30      SG4    大蒜-蔥蒜         900        屏東市          NaN   
10776  110.12.31      SG4    大蒜-蔥蒜         900        屏東市         75.0   

       Middle_Price  Lower_Price  Avg_Price  Trans_Quantity _merge  
1               NaN          NaN        NaN             NaN    NaN  
14              NaN          NaN        NaN             NaN    NaN  
21              NaN          NaN        NaN             NaN    NaN  
26              NaN          NaN        NaN             NaN    NaN  
34              NaN          NaN        NaN             NaN    NaN  
...             ...          ...        ...             ...    ...  
10747           NaN          NaN        NaN             NaN    NaN  
10756         119.0         76.2      115.0           380.0   both  
10765           NaN          NaN        NaN             NaN    NaN  
10767           NaN          NaN        NaN             NaN    NaN  
10776          75.0         75.0       75.0            20.0   both  

[1492 rows x 11 columns]

In [112]:
c = 0
for date in date_list:
    if date in rest_market['屏東市']:
        continue
    else:
        c += 1
        fil = dff[(dff['CropCode']=='SG1') & (dff['TransDate']==date)]
        if len(fil)!=1:
            print(fil)
            print(date)
print(c)

1492


In [88]:
dff.drop_duplicates(subset=['TransDate','CropCode'],inplace=True)

In [93]:
for index,row in dff[dff['CropCode']=='SG5'].iterrows():
    if row['TransDate'] in rest_market['屏東市']:
#         continue
#     if row['TransDate'] in date_list:
#         continue
#     else:
        print(row['TransDate'])

107.09.24


In [ ]:
len()